![Universidad Central](https://www.radcolombia.org/web/sites/default/files/archivos/instituciones/universidad-santo-tomas/logo-usta.png)

----


# **TALLER**



## Integrante:

* Mayumi Alejandra Sanchez
<mayumisanchez@usantotomas.edu.co>

* Paula Andrea Amortegui
<paulaamortegui@usantotomas.edu.co>
---

In [ ]:
import numpy as np
import pandas as pd

# Definir la función de pérdida
def loss_func(theta):
    x, y = theta
    R = np.sqrt(x**2 + y**2)
    return -np.sin(R)

# Definir el gradiente de la función de pérdida
def evaluate_gradient(theta):
    x, y = theta
    R = np.sqrt(x**2 + y**2)
    if R == 0:
        return np.zeros_like(theta)  # Evitar división por cero
    grad_x = -np.cos(R) * (x / R)
    grad_y = -np.cos(R) * (y / R)
    return np.array([grad_x, grad_y])

# Gradiente descendente
def gd(theta, epochs, eta):
    for i in range(epochs):
        gradient = evaluate_gradient(theta)
        theta -= eta * gradient
    dist = np.linalg.norm(theta)
    return theta, dist

# Gradiente descendente estocástico
def sgd(theta, data_train, epochs, eta):
    for i in range(epochs):
        np.random.shuffle(data_train)
        for example in data_train:
            gradient = evaluate_gradient(example)  # Usar el ejemplo
            theta -= eta * gradient
    dist = np.linalg.norm(theta)
    return theta, dist

# RMSprop
def rmsprop(theta, data_train, epochs, eta=0.001, decay=0.9, epsilon=1e-8):
    E_g2 = np.zeros_like(theta)
    for epoch in range(epochs):
        np.random.shuffle(data_train)
        for example in data_train:
            gradient = evaluate_gradient(example)  # Usar el ejemplo
            E_g2 = decay * E_g2 + (1 - decay) * gradient**2
            theta -= eta / (np.sqrt(E_g2) + epsilon) * gradient
    dist = np.linalg.norm(theta)
    return theta, dist

# Algoritmo Adam
def adam(theta, data_train, epochs, alpha=0.001, beta1=0.9, beta2=0.999, epsilon=1e-8):
    m = np.zeros_like(theta)
    v = np.zeros_like(theta)
    t = 0
    for epoch in range(epochs):
        np.random.shuffle(data_train)
        for example in data_train:
            t += 1
            gradient = evaluate_gradient(example)  # Usar el ejemplo
            m = beta1 * m + (1 - beta1) * gradient
            v = beta2 * v + (1 - beta2) * (gradient**2)
            m_hat = m / (1 - beta1**t)
            v_hat = v / (1 - beta2**t)
            theta -= alpha * m_hat / (np.sqrt(v_hat) + epsilon)
    dist = np.linalg.norm(theta)
    return theta, dist

# Inicialización de datos
np.random.seed(1006093739)
x_train = np.random.uniform(-6.5, 6.5, 100)
y_train = np.random.uniform(-6.5, 6.5, 100)
data_train = list(zip(x_train, y_train))

num_iterations = 10000
distancias = pd.DataFrame(np.zeros((num_iterations, 4)), columns=['GD', 'SGD', 'RMSPROP', 'Adam'])

for i in range(num_iterations):
    theta_init = np.random.uniform(-6.5, 6.5, 2)  # Nueva inicialización aleatoria en cada iteración

    theta_gd, distancias.at[i, 'GD'] = gd(theta_init.copy(), 1000, 0.1)
    theta_sgd, distancias.at[i, 'SGD'] = sgd(theta_init.copy(), data_train, 100, 0.01)
    theta_rmsprop, distancias.at[i, 'RMSPROP'] = rmsprop(theta_init.copy(), data_train, 100, 0.001, 0.9, 1e-8)
    theta_adam, distancias.at[i, 'Adam'] = adam(theta_init.copy(), data_train, 100, 0.001, 0.9, 0.999, 1e-8)

# Función para resaltar el valor mínimo de cada fila
def highlight_min(s):
    is_min = s == s.min()
    return ['background-color: lightgreen' if v else '' for v in is_min]
distancias_1 = distancias.style.apply(highlight_min, axis=1)

# Mostrar el DataFrame estilizado
distancias_1

In [12]:
import numpy as np
import pandas as pd
minimos_por_fila = distancias.idxmin(axis=1)

# Tabla de frecuencias absoluta y relativa
frecuencias_abs = minimos_por_fila.value_counts()
frecuencias_rel = minimos_por_fila.value_counts(normalize=True)

# Crear una tabla comparativa
tabla_frecuencias = pd.DataFrame({
    'Frecuencia Absoluta': frecuencias_abs,
    'Frecuencia Relativa': frecuencias_rel
})

# Encontrar el mejor optimizador
mejor_optimizador = tabla_frecuencias['Frecuencia Relativa'].idxmax()

# Mostrar resultados
print("Tabla de frecuencias absoluta y relativa:")
print(tabla_frecuencias)
print(f"\nEl mejor optimizador es: {mejor_optimizador}")

Tabla de frecuencias absoluta y relativa:
         Frecuencia Absoluta  Frecuencia Relativa
GD                      4460               0.4460
RMSPROP                 2675               0.2675
SGD                     1701               0.1701
Adam                    1164               0.1164

El mejor optimizador es: GD
